Merge Movie Financial Data with Genre Data in a new dataframe.  Missing data will be queried from TMDB using their API.  The resulting dataframe will be saved in a CSV file for analysis.

In [1]:
import pandas as pd
import requests
import json
import math
import warnings
import time

In [ ]:
DATA_PATH = '../datasets/'

In [2]:
def get_keys(path):
    """Get the API Key in the file indictated by the path parameter"""
    with open(path) as f:
        return json.load(f)

# Read in the Data from its CSVs

In [3]:
last_20_years_movie_budgets_df = pd.read_csv(DATA_PATH + 'last_20_years_movie_budgets.csv')

In [4]:
clean_tmdb_movies_df = pd.read_csv(DATA_PATH + 'clean_tmdb_movies.csv')

# Merge Available Data

do a left join so that none of the budget/profit data is lost and then attempt to fill in the genre data

## Left Join

In [5]:
bud_prof_genres_df = pd.merge(last_20_years_movie_budgets_df, clean_tmdb_movies_df, how='left', 
                              left_on=['movie', 'release_year'], right_on=['original_title', 'release_year'])

## Look at the Data

In [6]:
bud_prof_genres_df[['movie','title', 
                    'real_production_budget', 'real_domestic_gross', 'real_worldwide_gross', 'real_profit',
                    'genre_ids']]

movie title  real_production_budget  \
0                        My Dog Skip   NaN            1.039256e+07   
1                        Next Friday   NaN            1.410419e+07   
2                      The Terrorist   NaN            3.711629e+04   
3                          Supernova   NaN            8.907909e+07   
4                The Boondock Saints   NaN            1.039256e+07   
...                              ...   ...                     ...   
4000                         Aladdin   NaN            1.820000e+08   
4001                      BrightBurn   NaN            7.000000e+06   
4002                       Rocketman   NaN            4.100000e+07   
4003  Godzilla: King of the Monsters   NaN            1.700000e+08   
4004                              MA   NaN            5.000000e+06   

      real_domestic_gross  real_worldwide_gross   real_profit genre_ids  
0            5.062608e+07          5.314358e+07  4.275102e+07       NaN  
1            8.488730e+07          8.859704e+07  7.449285e+07       NaN  
2            2.895709e+05          2.895709e+05  2.524546e+05       NaN  
3            2.111006e+07          2.199733e+07 -6.708176e+07       NaN  
4            4.523882e+04          6.114894e+05 -9.781072e+06       NaN  
...                   ...                   ...           ...       ...  
4000         2.467343e+08          6.192343e+08  4.372343e+08       NaN  
4001         1.679443e+07          2.798950e+07  2.098950e+07       NaN  
4002         5.734272e+07          1.086427e+08  6.764272e+07       NaN  
4003         8.557694e+07          2.992769e+08  1.292769e+08       NaN  
4004         3.604954e+07          4.430062e+07  3.930062e+07       NaN  

[4005 rows x 7 columns]

Check to see how many rows are missing Genre Info

In [7]:
bud_prof_genres_df['genre_ids'].isna().sum()

2431

## Gather Missing Genre Ids

After doing a merge of the Budgets/Profit dataframe with the TMDB movies dataframe about half of the movies with a budget didn't merge with the TMDB dataframe

**Why?** Are they not in the TMDB dataframe, or is there a slight difference in the title?  Also, can the data be retrieved from the TMDB api to fill in the missing information?

In [8]:
# let's check the first movie
# are there any movies with the word 'dog' in the TMDB dataframe?
clean_tmdb_movies_df[clean_tmdb_movies_df['original_title'].str.contains('Skip|skip')]

Unnamed: 0  Unnamed: 0.1           genre_ids      id original_language  \
1294         1306          1306                  []  473553                en   
17416       17493         17493  [28, 35, 53, 9648]  270774                en   

        original_title  popularity release_date            title  \
1294   Sundance Skippy       1.114   2010-01-21  Sundance Skippy   
17416        Skiptrace      12.525   2016-09-02        Skiptrace   

       vote_average  vote_count  release_year  
1294            8.0           5          2010  
17416           5.6         324          2016

In [9]:
clean_tmdb_movies_df[clean_tmdb_movies_df['title'].str.contains('Skip|skip')]

Unnamed: 0  Unnamed: 0.1           genre_ids      id original_language  \
1294         1306          1306                  []  473553                en   
17416       17493         17493  [28, 35, 53, 9648]  270774                en   

        original_title  popularity release_date            title  \
1294   Sundance Skippy       1.114   2010-01-21  Sundance Skippy   
17416        Skiptrace      12.525   2016-09-02        Skiptrace   

       vote_average  vote_count  release_year  
1294            8.0           5          2010  
17416           5.6         324          2016

The first movie doesn't appeal to be in the TMDB dataframe, but it is on the TMDB site, so it can be queried to get its data

**What is the best way to get this data using the API?**

I will iterate through the new dataframe and query the API for the missing data, and then see what is still missing

In [10]:
bud_prof_genres_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4005 entries, 0 to 4004
Data columns (total 24 columns):
Unnamed: 0_x              4005 non-null int64
id_x                      4005 non-null int64
release_date_x            4005 non-null object
movie                     4005 non-null object
production_budget         4005 non-null int64
domestic_gross            4005 non-null int64
worldwide_gross           4005 non-null int64
release_year              4005 non-null int64
real_production_budget    4005 non-null float64
real_domestic_gross       4005 non-null float64
real_worldwide_gross      4005 non-null float64
real_profit               4005 non-null float64
real_margin               4005 non-null float64
Unnamed: 0_y              1574 non-null float64
Unnamed: 0.1              1574 non-null float64
genre_ids                 1574 non-null object
id_y                      1574 non-null float64
original_language         1574 non-null object
original_title            1574 non-null objec

### Create a mask for the missing Genre ID's

In [11]:
bud_prof_genres_df.genre_ids.unique()

array([nan, '[80, 18, 878, 53]', '[18, 10402]', '[28, 18, 53, 10752]',
       '[28, 18, 9648, 53]', '[80, 53]', '[27, 12, 28]', '[28, 18, 53]',
       '[27, 9648, 80]', '[878, 28, 27, 53, 12, 14]', '[12, 35, 10751]',
       '[18, 53]', '[10749, 35]', '[12, 14]', '[12, 16, 10751]', '[35]',
       '[28, 12, 14, 878]', '[28, 35, 10751]', '[28, 53, 878]',
       '[35, 10751, 14]', '[18]', '[27]', '[80, 18, 9648, 53]',
       '[18, 10749, 10752]', '[12, 14, 10751]', '[35, 10749]',
       '[53, 9648]', '[18, 53, 9648]', '[18, 28, 35, 80]', '[18, 80]',
       '[28, 35, 80]', '[9648, 27, 28]', '[10751, 14, 12]', '[]',
       '[10752, 28, 12, 18, 53]', '[18, 10749]', '[28, 35, 18]',
       '[28, 878, 53, 80]', '[35, 10751]', '[878, 35, 12]',
       '[80, 53, 35, 9648]', '[14, 12, 16, 10751]', '[18, 10751, 10749]',
       '[12, 14, 28]', '[35, 80, 53]', '[18, 10751]',
       '[80, 18, 9648, 10749]', '[35, 18]', '[28, 80]', '[99, 10751]',
       '[28, 12, 80, 9648, 53]', '[53, 80, 18, 28]', '[27,

NaN was being stored as a Float initially, so a work around was made to identify the NaN values.

In [6]:
nan = bud_prof_genres_df.genre_ids.unique()[0]

In [7]:
type(nan)

str

In [8]:
# check that nan will return True (it is NaN)
math.isnan(nan)

TypeError: must be real number, not str

In [15]:
def is_nan(x):
    """Return Boolean of whether the input value is NaN"""
    if type(x) == type(1.9):
        return math.isnan(x)
    else:
        return False

In [16]:
mask = bud_prof_genres_df.genre_ids.apply(is_nan)

Look at the results of the mask

In [17]:
bud_prof_genres_df.genre_ids[mask].unique()

array([nan], dtype=object)

## Gather Data with API
Now that the mask has been created, it's time to gather the genre data using the TMDB API and add it to the active dataframe

In [3]:
# get the api key
# note that the location of the API key on your system will be different
keys = get_keys('/Users/freethrall/.secret/tmdb_api.json')
api_key = keys['api_key']

# url of the movie database api for genres
url = 'https://api.themoviedb.org/3/search/movie'

def get_genre_ids(movie):
    """Return the genre_ids of the parameter movie, will use TMDB API if neccessary"""
    
    movie_title = movie.movie

    parameters = {'api_key': api_key,
                 'language': 'en-US',
                 'query': movie_title}

    # get the current time
    t0 = time.time()
    
    r = requests.get(url, params=parameters)
    
    # the delay is the current time - t0 (the previous time)
    response_delay = time.time() - t0
    
    # wait 10x longer than it took them to respond
    time.sleep(10*response_delay)  
    
    if r.status_code != 200: #there was a problem
        warnings.warn(f'There was a problem with {movie_title}, status code {r.status_code}')
        return None
    else:
        results = pd.DataFrame.from_dict(r.json()['results'])
        
        if len(results) == 0: # the movie data is not available
            print(f'Genre Data not available for {movie_title}')
            return None
        else:
            genre_id_list = str(results['genre_ids'][0])
                
            return genre_id_list
    
 

In [19]:
bud_prof_genres_df.genre_ids[mask] = bud_prof_genres_df[mask].apply(get_genre_ids, axis=1)
bud_prof_genres_df

Genre Data not available for Hum to Mohabbt Karega
Genre Data not available for AimÃ©e & Jaguar
Genre Data not available for The Widow of St. Pierre
Genre Data not available for A Knightâs Tale
Genre Data not available for John Carpenterâs Ghosts of Mars
Genre Data not available for Donât Say a Word
Genre Data not available for Le Fabuleux destin d'AmÃ©lie Poulain
Genre Data not available for Keeping it Real: The Adventures of Greg Walloch
Genre Data not available for Harry Potter and the Sorcererâs Stone
Genre Data not available for Y Tu MamÃ¡ TambiÃ©n
Genre Data not available for National Lampoonâs Van Wilder
Genre Data not available for The Business of Fancy Dancing
Genre Data not available for Star Wars Ep. II: Attack of the Clones
Genre Data not available for The Divine Secrets of the Ya-Ya Sisterhood
Genre Data not available for Wes Craven Presents: They
Genre Data not available for Steal (Canadian Release)
Genre Data not available for 28 Days Laterâ¦
Genre Data not av

/Users/freethrall/anaconda3/envs/learn-env/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


Unnamed: 0_x  id_x release_date_x                           movie  \
0             3994    95     2000-01-12                     My Dog Skip   
1             3752    53     2000-01-12                     Next Friday   
2             5747    48     2000-01-14                   The Terrorist   
3              940    41     2000-01-14                       Supernova   
4             4060    61     2000-01-21             The Boondock Saints   
...            ...   ...            ...                             ...   
4000            80    81     2019-05-24                         Aladdin   
4001          4012    13     2019-05-24                      BrightBurn   
4002          1370    71     2019-05-31                       Rocketman   
4003           124    25     2019-05-31  Godzilla: King of the Monsters   
4004          4265    66     2019-05-31                              MA   

      production_budget  domestic_gross  worldwide_gross  release_year  \
0               7000000        34099640         35795319          2000   
1               9500000        57176582         59675307          2000   
2                 25000          195043           195043          2000   
3              60000000        14218868         14816494          2000   
4               7000000           30471           411874          2000   
...                 ...             ...              ...           ...   
4000          182000000       246734314        619234314          2019   
4001            7000000        16794432         27989498          2019   
4002           41000000        57342725        108642725          2019   
4003          170000000        85576941        299276941          2019   
4004            5000000        36049540         44300625          2019   

      real_production_budget  real_domestic_gross  ...  Unnamed: 0.1  \
0               1.039256e+07         5.062608e+07  ...           NaN   
1               1.410419e+07         8.488730e+07  ...           NaN   
2               3.711629e+04         2.895709e+05  ...           NaN   
3               8.907909e+07         2.111006e+07  ...           NaN   
4               1.039256e+07         4.523882e+04  ...           NaN   
...                      ...                  ...  ...           ...   
4000            1.820000e+08         2.467343e+08  ...           NaN   
4001            7.000000e+06         1.679443e+07  ...           NaN   
4002            4.100000e+07         5.734272e+07  ...           NaN   
4003            1.700000e+08         8.557694e+07  ...           NaN   
4004            5.000000e+06         3.604954e+07  ...           NaN   

                       genre_ids  id_y  original_language  original_title  \
0                       [35, 18]   NaN                NaN             NaN   
1                           [35]   NaN                NaN             NaN   
2                           [99]   NaN                NaN             NaN   
3                  [27, 878, 53]   NaN                NaN             NaN   
4                   [28, 80, 53]   NaN                NaN             NaN   
...                          ...   ...                ...             ...   
4000  [12, 35, 14, 10749, 10751]   NaN                NaN             NaN   
4001               [27, 878, 53]   NaN                NaN             NaN   
4002                        [18]   NaN                NaN             NaN   
4003                   [28, 878]   NaN                NaN             NaN   
4004                        [27]   NaN                NaN             NaN   

     popularity  release_date_y title vote_average  vote_count  
0           NaN             NaN   NaN          NaN         NaN  
1           NaN             NaN   NaN          NaN         NaN  
2           NaN             NaN   NaN          NaN         NaN  
3           NaN             NaN   NaN          NaN         NaN  
4           NaN             NaN   NaN          NaN         NaN  
...         ...             ...   ..

Save the dataframe as a CSV file

In [20]:
bud_prof_genres_df.to_csv(DATA_PATH + 'financials_with_genres.csv')

## Massage the titles that should have data but didn't return any

read in the current data

In [5]:
bud_prof_genres_df = pd.read_csv(DATA_PATH + 'financials_with_genres.csv')

### create a mask for the rows that are still missing genre data

In [10]:
mask2 = bud_prof_genres_df.genre_ids.isna()

In [12]:
mask2.value_counts()

False    3896
True      109
Name: genre_ids, dtype: int64

In [ ]:
pd.set_option('display.max_rows', None)

In [27]:
bud_prof_genres_df.at[70, 'movie'] = 'Hum to Mohabbat Karega'

In [25]:
bud_prof_genres_df.at[101, 'movie'] = 'Aimee & Jaguar'

In [29]:
bud_prof_genres_df.at[242, 'movie'] = "A Knight's Tale"

In [30]:
bud_prof_genres_df.at[294, 'movie'] = "John Carpenter's Ghosts of Mars"

In [31]:
bud_prof_genres_df.at[309, 'movie'] = "Don't Say a Word"

In [32]:
bud_prof_genres_df.at[337, 'movie'] = "Harry Potter and the Sorcerer's Stone"

In [33]:
bud_prof_genres_df.at[432, 'movie'] = 'Star Wars Episode. II: Attack of the Clones'

In [34]:
bud_prof_genres_df.at[1039, 'movie'] = 'Star Wars Episode III: Revenge of the Sith'

In [35]:
bud_prof_genres_df.at[1302, 'movie'] = "Pirates of the Caribbean: Dead Man's Chest"

In [36]:
bud_prof_genres_df.at[1496, 'movie'] = "Pirates of the Caribbean: At World's End"

In [37]:
bud_prof_genres_df.at[2434, 'movie'] = "Harry Potter and the Deathly Hallows: Part 2"

In [38]:
bud_prof_genres_df.at[2586, 'movie'] = 'The Lorax'

In [39]:
bud_prof_genres_df.at[3394, 'movie'] = 'Star Wars Episode VII: The Force Awakens'

In [40]:
bud_prof_genres_df.at[3811, 'movie'] = 'Star Wars Episode VIII: The Last Jedi'

In [41]:
bud_prof_genres_df.at[3939, 'movie'] = 'The Grinch'

In [45]:
bud_prof_genres_df.at[3953, 'movie'] = 'Spider-Man: Into The Spider-Verse'

In [46]:
bud_prof_genres_df.at[3997, 'movie'] = 'Pokémon Detective Pikachu'

In [47]:
print(bud_prof_genres_df[mask2]['movie'])

70                                 Hum to Mohabbat Karega
101                                        Aimee & Jaguar
207                               The Widow of St. Pierre
242                                       A Knight's Tale
294                       John Carpenter's Ghosts of Mars
309                                      Don't Say a Word
330                  Le Fabuleux destin d'AmÃ©lie Poulain
334       Keeping it Real: The Adventures of Greg Walloch
337                 Harry Potter and the Sorcerer's Stone
402                                   Y Tu MamÃ¡ TambiÃ©n
412                       National Lampoonâs Van Wilder
431                         The Business of Fancy Dancing
432           Star Wars Episode. II: Attack of the Clones
444            The Divine Secrets of the Ya-Ya Sisterhood
546                             Wes Craven Presents: They
632                              Steal (Canadian Release)
662                                      28 Days Laterâ¦
776           

### Run The API with the Updated List

In [48]:
bud_prof_genres_df.genre_ids[mask2] = bud_prof_genres_df[mask2].apply(get_genre_ids, axis=1)
bud_prof_genres_df

Genre Data not available for The Widow of St. Pierre
Genre Data not available for Le Fabuleux destin d'AmÃ©lie Poulain
Genre Data not available for Keeping it Real: The Adventures of Greg Walloch
Genre Data not available for Y Tu MamÃ¡ TambiÃ©n
Genre Data not available for National Lampoonâs Van Wilder
Genre Data not available for The Business of Fancy Dancing
Genre Data not available for The Divine Secrets of the Ya-Ya Sisterhood
Genre Data not available for Wes Craven Presents: They
Genre Data not available for Steal (Canadian Release)
Genre Data not available for 28 Days Laterâ¦
Genre Data not available for Teacher's Pet: The Movie
Genre Data not available for Tae Guik Gi: The Brotherhood of War
Genre Data not available for La mala educaciÃ³n
Genre Data not available for Un long dimanche de fianÃ§ailles
Genre Data not available for The Mongol King
Genre Data not available for The Helixâ¦Loaded
Genre Data not available for De battre mon coeur s'est arrÃªtÃ©
Genre Data not availab

/Users/freethrall/anaconda3/envs/learn-env/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


Unnamed: 0  Unnamed: 0_x  id_x release_date_x  \
0              0          3994    95     2000-01-12   
1              1          3752    53     2000-01-12   
2              2          5747    48     2000-01-14   
3              3           940    41     2000-01-14   
4              4          4060    61     2000-01-21   
5              5          3780    81     2000-01-21   
6              6          1618    19     2000-01-28   
7              7          4535    36     2000-01-28   
8              8          3077    78     2000-01-28   
9              9          3685    86     2000-02-04   
10            10          1397    98     2000-02-04   
11            11          1150    51     2000-02-11   
12            12          5619    20     2000-02-11   
13            13          3250    51     2000-02-11   
14            14          2532    33     2000-02-11   
15            15          2376    77     2000-02-18   
16            16          3783    84     2000-02-18   
17            17          1462    63     2000-02-18   
18            18          2337    38     2000-02-18   
19            19          1712    13     2000-02-23   
20            20          1614    15     2000-02-25   
21            21          4500     1     2000-03-01   
22            22          2953    54     2000-03-03   
23            23          4921    22     2000-03-03   
24            24          2266    67     2000-03-03   
25            25          1200     1     2000-03-03   
26            26          5541    42     2000-03-10   
27            27          1573    74     2000-03-10   
28            28          5364    65     2000-03-10   
29            29           468    69     2000-03-10   
30            30          1094    95     2000-03-17   
31            31          2373    74     2000-03-17   
32            32          2188    89     2000-03-22   
33            33          3097    98     2000-03-24   
34            34          3106     7     2000-03-24   
35            35          3036    37     2000-03-31   
36            36          2570    71     2000-03-31   
37            37           420    21     2000-03-31   
38            38          3660    61     2000-04-05   
39            39           880    81     2000-04-07   
40            40          2345    46     2000-04-07   
41            41          2356    57     2000-04-07   
42            42          2019    20     2000-04-14   
43            43          1336    37     2000-04-14   
44            44          4710    11     2000-04-14   
45            45          3891    92     2000-04-14   
46            46          4613    14     2000-04-19   
47            47           830    31     2000-04-21   
48            48          3055    56     2000-04-21   
49            49          4154    55     2000-04-21   
50            50          3213    14     2000-04-21   
51            51          1830    31     2000-04-28   
52            52           963    64     2000-04-28   
53            53          3041    42     2000-04-28   
54            54          4009    10     2000-05-05   
55            55          5136    37     2000-05-05   
56            56          4645    46     2000-05-05   
57            57          5268    69     2000-05-05   
58            58          1766    67     2000-05-05   
59            59           355    56     2000-05-05   
60            60          3903     4     2000-05-12   
61            61           597    98     2000-05-12   
62            62          3410    11     2000-05-12   
63            63          2807     8     2000-05-12   
64            64          4933    34     2000-05-12   
65            65           257    58     2000-05-19   
66            66          2929    30     2000-05-19   
67            67          2806     7     2000-05-19   
68            68           283    84     2000-05-24   
69            69          1013    14     2000-05-26   
70            70          4952    53     2000-05-26   
71            71          1770    71     2000-

In [49]:
bud_prof_genres_df.genre_ids.isna().value_counts()

False    3913
True       92
Name: genre_ids, dtype: int64

The 17 corrected titles now have genre data

### Save the updated dataframe

In [50]:
bud_prof_genres_df.to_csv(DATA_PATH + 'financials_with_genres.csv')